In [1]:
# IMPORTING LIBRARIES

import sys
IN_COLAB = "google.colab" in sys.modules

import gym
import numpy as np

import tensorflow as tf
import tensorflow_probability as tfp
from tensorflow.keras import optimizers, losses
from tensorflow.keras import Model

from IPython.display import clear_output

class Network(Model):
    def __init__(self, state_size: int, action_size: int, 
    ):
        """Initialization."""
        super(Network, self).__init__()
        
        self.state_size = state_size
        self.action_size = action_size
        # set the hidden layers
        self.layer1 = tf.keras.layers.Dense(hidden_size, activation='relu')
        self.layer2 = tf.keras.layers.Dense(hidden_size, activation='relu')
        self.policy = tf.keras.layers.Dense(self.action_size,activation='softmax')

    def call(self, state):
        layer1 = self.layer1(state)
        layer2 = self.layer2(layer1)
        policy = self.policy(layer2)
        return policy

class DQNAgent:
    """A2CAgent interacting with environment.
        
    Attributes:
        env (gym.Env): openAI Gym environment
        gamma (float): discount factor
        entropy_weight (float): rate of weighting entropy into the loss function
        actor (tf.keras.Model): target actor model to select actions
        critic (tf.keras.Model): critic model to predict state values
        actor_optimizer (optim.Optimizer) : optimizer of actor
        critic_optimizer (optim.Optimizer) : optimizer of critic
        transition (list): temporory storage for the recent transition
        is_test (bool): flag to show the current mode (train / test)
    """

    def __init__(
        self, 
        env: gym.Env,
    ):
        """Initialization.
        
        Args:
            env (gym.Env): openAI Gym environment
            gamma (float): discount factor
        """
        
        # CREATING THE Q-Network
        self.env = env
        
        self.state_size = self.env.observation_space.shape[0]
        self.action_size = self.env.action_space.n
        
        self.lr = 7e-3
        self.gamma = 0.99    # discount rate
        self.model = Network(self.state_size, self.action_size
                          )
        self.optimizers = optimizers.Adam(lr=self.lr, )
        self.log_prob = None
    
    def get_action(self, state):
        #print("-------------------get_action---------------------------")
        #print("state : ", state)
        
        prob = self.model(np.array([state]))
        #print("prob = self.model(np.array([state])) -> ",prob)
        
        prob = prob.numpy()
        #print("prob = prob.numpy() -> ",prob)
        
        
        dist = tfp.distributions.Categorical(probs=prob, dtype=tf.float32)
        #print("dist = tfp.distributions.Categorical(probs=prob, dtype=tf.float32) -> ",dist)
        
        
        action = dist.sample()
        #print("action = dist.sample() -> ",action)
        return int(action.numpy()[0])
    
    def actor_loss(self,prob, action, discnt_reward): 
        #print("action : ", action)
        #print("prob : ",prob)
        dist = tfp.distributions.Categorical(probs=prob, dtype=tf.float32)
        #print("dist : ",dist)
        log_prob = dist.log_prob(action)
        #print("log_prob : ",log_prob)
        loss = -log_prob*discnt_reward
        return loss
    
    def n_step_td_target(self, states, actions, rewards, gamma):
        R_to_Go = 0
        discnt_rewards = []
        rewards.reverse()
        #print("rewards.shape :  ",len(rewards))
        #print("rewards : ",rewards)
        
        for r in rewards:
            R_to_Go = r + self.gamma*R_to_Go
            discnt_rewards.append(R_to_Go)
        discnt_rewards.reverse()
        #print("discnt_rewards :  ",discnt_rewards)
        states  = np.array(states, dtype=np.float32)
        actions = np.array(actions, dtype=np.int32)
        discnt_rewards = np.array(discnt_rewards, dtype=np.float32)
        
        return states, actions, discnt_rewards
        
    def train_step(self, states, actions, discnt_rewards):
        discnt_rewards = tf.reshape(discnt_rewards, (len(discnt_rewards),))
        
        dqn_variable = self.model.trainable_variables
        print("dqn_variable : ",dqn_variable)
        with tf.GradientTape() as tape:
            curr_Ps = self.model(states, training=True)
            print("curr_Ps : ",curr_Ps)
            loss = self.actor_loss(curr_Ps, actions, discnt_rewards)
            print("loss : ", loss)
            
        dqn_grads = tape.gradient(loss, dqn_variable)
        print("dqn_grads  : ",dqn_grads)
        print(zip(dqn_grads,dqn_variable))
        self.optimizers.apply_gradients(zip(dqn_grads, dqn_variable))
        
        return loss

seed = 12345
# CREATING THE ENVIRONMENT
env_name = "CartPole-v0"
env = gym.make(env_name)
env.seed(seed)     # reproducible, general Policy gradient has high variance

# INITIALIZING THE Q-PARAMETERS
hidden_size = 64
max_episodes = 300  # Set total number of episodes to train agent on.

# train
agent = DQNAgent(
    env, 
#     memory_size, 
#     batch_size, 
#     epsilon_decay,
)

if __name__ == "__main__":
    tf.random.set_seed(seed)
    # 2.5 TRAINING LOOP
    #List to contain all the rewards of all the episodes given to the agent
    scores = []
    
    # EACH EPISODE    
    for episode in range(max_episodes):
        ## Reset environment and get first new observation
        state = agent.env.reset()
        episode_reward = 0
        done = False  # has the enviroment finished?
        
        states  = []
        actions = []
        rewards = []
            
        # EACH TIME STEP    
        while not done:
        # for step in range(max_steps):  # step index, maximum step is 200
            action = agent.get_action(state)
            
            # TAKING ACTION
            next_state, reward, done, _ = agent.env.step(action)
            
            states.append(state)
            actions.append(action)
            rewards.append(reward)
            
            # Our new state is state
            state = next_state
            
            episode_reward += reward

            # if episode ends
            if done:
                scores.append(episode_reward)
                print("Episode " + str(episode+1) + ": " + str(episode_reward))
                
                states, actions, discnt_rewards = agent.n_step_td_target(states, actions, rewards, 1)
                loss = agent.train_step(states, actions, discnt_rewards) 
                break

C:\Users\CY-Kim\anaconda3\envs\neural\lib\site-packages\keras\optimizer_v2\optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


Episode 1: 8.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 0.27296162, -0.17804036, -0.07927951, -0.12425034,  0.2288279 ,
         0.11796519, -0.13276358,  0.09862167, -0.11458725,  0.16514203,
         0.26260436,  0.1192348 ,  0.13871145,  0.21713877, -0.22416733,
         0.01230967, -0.24634814,  0.0196003 , -0.22890171,  0.07949671,
        -0.02125752, -0.2962607 ,  0.07421681, -0.19659904, -0.29255104,
        -0.11174372, -0.02183038,  0.2079063 , -0.18454453,  0.03327066,
         0.05053812,  0.27724504, -0.0573011 , -0.22257146, -0.07126421,
        -0.00193298,  0.11802468,  0.10111982, -0.10187986,  0.25217706,
        -0.2050736 ,  0.09851778,  0.06388745, -0.15860102, -0.10116458,
        -0.24623576,  0.05661654, -0.00725624,  0.18742007, -0.05944464,
        -0.209663  ,  0.15087005,  0.10444012, -0.13430506,  0.22935003,
        -0.23247093,  0.02294299,  0.08034763,  0.18210009, -0.14215867,
        -0.2703808

Episode 3: 19.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 0.27469787, -0.17587131, -0.09206008, -0.12425034,  0.24145022,
         0.11796519, -0.14499667,  0.09526131, -0.11994284,  0.16690306,
         0.27653548,  0.11402658,  0.12711422,  0.22107363, -0.22937557,
         0.02481181, -0.2515554 ,  0.0196003 , -0.24137658,  0.08150718,
        -0.02546099, -0.28680497,  0.06900853, -0.20326705, -0.29775932,
        -0.11524726, -0.0270311 ,  0.2079063 , -0.19853131,  0.02845264,
         0.05053812,  0.26561996, -0.0446828 , -0.22257146, -0.05746152,
        -0.01559588,  0.12321524,  0.1118186 , -0.10187986,  0.25217706,
        -0.21028107,  0.10372405,  0.06665761, -0.16697356, -0.10637276,
        -0.23280385,  0.05329549, -0.00725624,  0.1917368 , -0.05647695,
        -0.22365016,  0.15607847,  0.10444012, -0.12909706,  0.22426276,
        -0.2462192 ,  0.03015322,  0.0746382 ,  0.18080114, -0.14480887,
        -0.282764

Episode 5: 33.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 2.64147729e-01, -1.84949562e-01, -1.02543123e-01,
        -1.15748793e-01,  2.35649183e-01,  1.13897584e-01,
        -1.47231594e-01,  1.05997935e-01, -1.26851603e-01,
         1.54995888e-01,  2.70963877e-01,  1.02889866e-01,
         1.19162858e-01,  2.22361118e-01, -2.39845619e-01,
         3.42670530e-02, -2.61318326e-01,  2.88513247e-02,
        -2.51827449e-01,  7.02618510e-02, -1.93021633e-02,
        -2.93885767e-01,  5.85674755e-02, -1.96818739e-01,
        -3.04103464e-01, -1.15728818e-01, -3.71304415e-02,
         1.98560312e-01, -2.09686130e-01,  1.99217759e-02,
         5.55669367e-02,  2.65863806e-01, -3.67743596e-02,
        -2.19837457e-01, -5.49641810e-02, -1.55725013e-02,
         1.23229064e-01,  1.18121110e-01, -9.27846134e-02,
         2.56244242e-01, -2.20472202e-01,  1.10363461e-01,
         5.54310307e-02, -1.58779278e-01, -1.17027223e-01,
        

Episode 8: 36.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 0.24840057, -0.19773921, -0.10691538, -0.10269605,  0.22187437,
         0.10207778, -0.1506233 ,  0.10491554, -0.1255722 ,  0.13996185,
         0.27519962,  0.08712543,  0.12797792,  0.23062707, -0.25559026,
         0.04607215, -0.2758091 ,  0.03990541, -0.25947458,  0.07114093,
        -0.00847674, -0.3013548 ,  0.04308603, -0.18484455, -0.3113891 ,
        -0.10741779, -0.05372028,  0.18530041, -0.21158248,  0.01222098,
         0.05233227,  0.27216417, -0.03351306, -0.21813942, -0.05021589,
        -0.01586057,  0.11087506,  0.12361123, -0.07973786,  0.24705209,
        -0.23570253,  0.11265267,  0.059306  , -0.15139745, -0.12561825,
        -0.21397074,  0.06669646, -0.03165442,  0.2049262 , -0.08104393,
        -0.23471262,  0.17248869,  0.12509869, -0.11863765,  0.22720768,
        -0.2558871 ,  0.01539325,  0.08314609,  0.19355023, -0.12306013,
        -0.275621

...

Episode 296: 57.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 1.40397340e-01, -2.20312551e-01, -1.72994629e-01,
        -9.56643447e-02,  1.87082365e-01,  6.53486401e-02,
        -1.66530415e-01,  7.16412887e-02, -1.10075727e-01,
         1.05969392e-01,  1.81574151e-01,  4.78713140e-02,
        -2.81732380e-02,  2.86247909e-01, -5.07234573e-01,
        -1.47805037e-02, -3.80772531e-01,  2.45128591e-02,
        -3.37919533e-01,  2.61796750e-02, -1.34764016e-01,
        -2.16659918e-01, -1.00662261e-01, -1.78233013e-01,
        -3.60898376e-01, -1.48695558e-01, -1.25496641e-01,
         9.98274013e-02, -2.55481124e-01, -6.62950426e-02,
         1.50687471e-02,  3.36328626e-01, -9.95744690e-02,
        -3.61710250e-01, -1.70979559e-01, -1.67462200e-01,
         1.33406473e-02, -7.99042583e-02, -3.14124107e-01,
         4.81006913e-02, -5.17358780e-01,  6.66575432e-02,
         4.62431274e-02, -1.20198652e-01, -4.18295979e-01,
      

Episode 297: 71.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 1.40797168e-01, -2.19686568e-01, -1.73074082e-01,
        -9.54677165e-02,  1.85741946e-01,  6.57019094e-02,
        -1.66832939e-01,  7.14723691e-02, -1.10103652e-01,
         1.05923533e-01,  1.80338576e-01,  4.84069623e-02,
        -2.81732380e-02,  2.86610872e-01, -5.06916761e-01,
        -1.44026717e-02, -3.80894572e-01,  2.50495095e-02,
        -3.37959975e-01,  2.61183493e-02, -1.34974405e-01,
        -2.16501892e-01, -1.00662284e-01, -1.78235307e-01,
        -3.60995173e-01, -1.48695558e-01, -1.25496641e-01,
         1.00252822e-01, -2.55505174e-01, -6.69338480e-02,
         1.55328950e-02,  3.36830318e-01, -9.95744690e-02,
        -3.61554235e-01, -1.70952946e-01, -1.67523056e-01,
         1.33406473e-02, -8.00755769e-02, -3.14029455e-01,
         4.81006913e-02, -5.17193556e-01,  6.70432299e-02,
         4.58599404e-02, -1.20818272e-01, -4.18050915e-01,
      

Episode 298: 71.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 1.41261190e-01, -2.19326958e-01, -1.73267946e-01,
        -9.52319130e-02,  1.84396505e-01,  6.60528317e-02,
        -1.67279825e-01,  7.11892769e-02, -1.10126391e-01,
         1.05882168e-01,  1.79146767e-01,  4.90121469e-02,
        -2.81732380e-02,  2.87002027e-01, -5.06488144e-01,
        -1.42532010e-02, -3.80830079e-01,  2.56526060e-02,
        -3.38123947e-01,  2.58563906e-02, -1.35243893e-01,
        -2.16562554e-01, -1.00662299e-01, -1.78258717e-01,
        -3.60936850e-01, -1.48695558e-01, -1.25496641e-01,
         1.00743383e-01, -2.55581170e-01, -6.76303133e-02,
         1.60767864e-02,  3.37403744e-01, -9.95744690e-02,
        -3.61311734e-01, -1.70991048e-01, -1.67664275e-01,
         1.33406473e-02, -8.03684667e-02, -3.13822150e-01,
         4.81006913e-02, -5.16896546e-01,  6.75013587e-02,
         4.53320742e-02, -1.21490359e-01, -4.17649806e-01,
      

Episode 299: 79.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 1.41744435e-01, -2.19037801e-01, -1.73484623e-01,
        -9.48974639e-02,  1.83063552e-01,  6.63720220e-02,
        -1.67733788e-01,  7.07709938e-02, -1.10155724e-01,
         1.05844863e-01,  1.77963659e-01,  4.96639423e-02,
        -2.81732380e-02,  2.87365079e-01, -5.05901098e-01,
        -1.42215807e-02, -3.80650043e-01,  2.63096429e-02,
        -3.38317752e-01,  2.54940018e-02, -1.35530874e-01,
        -2.16727853e-01, -1.00662313e-01, -1.78288624e-01,
        -3.60777646e-01, -1.48695558e-01, -1.25496641e-01,
         1.01244256e-01, -2.55688220e-01, -6.83158860e-02,
         1.66748874e-02,  3.37936640e-01, -9.95744690e-02,
        -3.60946238e-01, -1.71094209e-01, -1.67872712e-01,
         1.33406473e-02, -8.06881264e-02, -3.13444018e-01,
         4.81006913e-02, -5.16443193e-01,  6.80295676e-02,
         4.47457209e-02, -1.22161753e-01, -4.17074561e-01,
      

Episode 300: 55.0
dqn_variable :  [<tf.Variable 'network/dense/kernel:0' shape=(4, 64) dtype=float32, numpy=
array([[ 1.42182752e-01, -2.18778372e-01, -1.73649341e-01,
        -9.45019498e-02,  1.81866661e-01,  6.66367710e-02,
        -1.68091446e-01,  7.03259483e-02, -1.10185921e-01,
         1.05813906e-01,  1.76820904e-01,  5.02656177e-02,
        -2.81732380e-02,  2.87645817e-01, -5.05224526e-01,
        -1.42250899e-02, -3.80447358e-01,  2.69058682e-02,
        -3.38462681e-01,  2.52397321e-02, -1.35757864e-01,
        -2.16860205e-01, -1.00662328e-01, -1.78294212e-01,
        -3.60601723e-01, -1.48695558e-01, -1.25496641e-01,
         1.01704732e-01, -2.55779505e-01, -6.89150915e-02,
         1.72038972e-02,  3.38345081e-01, -9.95744690e-02,
        -3.60459059e-01, -1.71210632e-01, -1.68056652e-01,
         1.33406473e-02, -8.09263065e-02, -3.12975019e-01,
         4.81006913e-02, -5.15901804e-01,  6.85059130e-02,
         4.42738086e-02, -1.22705042e-01, -4.16346252e-01,
      